In [1]:
from human_aware_rl.utils import set_style
from human_aware_rl.experiments.bc_experiments import *
from human_aware_rl.experiments.pbt_experiments import *
from human_aware_rl.experiments.ppo_bc_experiments import *
from human_aware_rl.experiments.ppo_sp_experiments import *
from human_aware_rl.experiments.planning_experiments import P_BC_evaluation

best_bc_model_paths = load_pickle("data/bc_runs/best_bc_model_paths")
best_bc_models_performance = load_pickle("data/bc_runs/best_bc_models_performance")
set_style()

layouts = ['simple', 'unident_s']
delivery_horizon_dict = {"simple": 2, "unident_s": 3}

from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv
from overcooked_ai_py.agents.benchmarking import AgentEvaluator
from overcooked_ai_py.agents.agent import EmbeddedPlanningAgent, AgentPair

from human_aware_rl.imitation.behavioural_cloning import get_bc_agent_from_saved

import json, copy
import numpy as np

from overcooked_ai_py.utils import save_pickle, load_pickle, cumulative_rewards_from_rew_list, save_as_json, load_from_json
from overcooked_ai_py.planning.planners import NO_COUNTERS_PARAMS, MediumLevelPlanner
from overcooked_ai_py.mdp.layout_generator import LayoutGenerator
from overcooked_ai_py.agents.agent import AgentPair, CoupledPlanningAgent, RandomAgent, GreedyHumanModel
from overcooked_ai_py.mdp.overcooked_mdp import OvercookedGridworld, Action, OvercookedState
from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv



best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

set_global_seed(166)

/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/nils/minicond

In [2]:
# CP+HPROXY horizon 100
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Use keras.layers.flatten instead.
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.55 seconds,   	7797 state expanded (0.33 unique) 	 ~3061.16 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.30 seconds,   	7826 state expanded (0.32 unique) 	 ~3405.88 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.84 seconds,   	7776 state expanded (0.33 unique) 	 ~2735.46 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.59 seconds,   	7591 state expanded (0.32 unique) 	 ~2926.53 expansions/s
First m

/home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/mdp/overcooked_env.py:162: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return np.array(trajectory), self.t, self.cumulative_sparse_rewards, self.cumulative_shaped_rewards
100%|█████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:51<00:00, 51.84s/it]

Timestep: 81
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X ←o    X 
X D X S X 


Path for last node expanded:  [None, (((1, 2), (0, 1)), ((2, 1), (0, -1))), (((1, 2), (0, 1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((1, 2) facing (0, 1) holding onion@(1, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((1, 2), (0, 1)), ((2, 1), (0, -1))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f69883deb90>, 1)]
COUPLED PLANNING FAILURE
failures:  60
Timestep: 82
Joint action taken: ('→', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   →o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (1, 0) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('

...

Found goal after: 	5.86 seconds,   	17572 state expanded (0.37 unique) 	 ~3000.66 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ←o    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	6.75 seconds,   	18626 state expanded (0.37 unique) 	 ~2759.57 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	10.97 seconds,   	18625 state expanded (0.37 unique) 	 ~1697.99 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-↑0    X 
X       ø20      X 
X X X D 

Found goal after: 	7.71 seconds,   	22511 state expanded (0.36 unique) 	 ~2918.13 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø17      X 
X ↓o    P ↓o    X 
X X X D X D X X X 


Found goal after: 	7.84 seconds,   	22963 state expanded (0.36 unique) 	 ~2930.59 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø18      X 
X   →o  P ←o    X 
X X X D X D X X X 


Found goal after: 	7.44 seconds,   	22963 state expanded (0.36 unique) 	 ~3087.91 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø19      X 
X     →oø-←0    X 
X X X D X D X X

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [16:01<00:00, 961.97s/it]

Found goal after: 	0.11 seconds,   	308 state expanded (0.49 unique) 	 ~2703.77 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 96
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑dø20      X 
X       ø15←d    X 
X X X D X D X X X 


Found goal after: 	0.07 seconds,   	211 state expanded (0.56 unique) 	 ~3093.57 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 97
Joint action taken: ('↑', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20↑d    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	67 state expanded (0.79 unique) 	 ~2266.59 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 98
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20←d    X 
X       ø17      X 
X X X D X D X X 

{'simple': 0.0, 'unident_s': 40.0}

In [3]:
# CP+HPROXY switched indices horizon 100
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.84 seconds,   	7797 state expanded (0.33 unique) 	 ~2746.00 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	3.56 seconds,   	7842 state expanded (0.32 unique) 	 ~2201.79 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	2.86 seconds,   	7612 state expanded (0.32 unique) 	 ~2665.82 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	3.13 seconds,   	7702 state expanded (0.32 unique) 	 ~2461.03 expansions/s
First mo

Found goal after: 	1.17 seconds,   	3383 state expanded (0.33 unique) 	 ~2890.96 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.23 seconds,   	3381 state expanded (0.33 unique) 	 ~2757.99 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.20 seconds,   	3379 state expanded (0.33 unique) 	 ~2819.02 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.16 seconds,   	3377 state expanded (0.33 unique) 	 ~2917.11 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.92 seconds,   	5617 state expanded (0.33 unique) 	 ~2923.56 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	2.04 seconds,   	5261 state expanded (0.33 unique) 	 ~2578.49 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.86 seconds,   	5188 state expanded (0.33 unique) 	 ~2789.98 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.84 seconds,   	5353 state expanded (0.33 unique) 	 ~2909.32 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	1.08 seconds,   	3852 state expanded (0.37 unique) 	 ~3577.67 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø6      X 
X       ø20↓d    X 
X X X D X D X X X 


Found goal after: 	0.59 seconds,   	2015 state expanded (0.35 unique) 	 ~3404.81 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø7↑d    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.50 seconds,   	1716 state expanded (0.36 unique) 	 ~3440.19 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø8↑d    X 
X       ø20      X 
X

Found goal after: 	37.87 seconds,   	87961 state expanded (0.35 unique) 	 ~2322.64 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('→', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø-    →sX 
X       P       X 
X X X D X D X X X 


Found goal after: 	15.89 seconds,   	44530 state expanded (0.35 unique) 	 ~2802.61 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('↑', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X ↑sS 
X   ←1  ø-      X 
X       P       X 
X X X D X D X X X 


Found goal after: 	18.21 seconds,   	47192 state expanded (0.35 unique) 	 ~2592.02 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('→', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X →sS 
X ←1    ø-      X 
X       P       X 
X X X D X D X X 

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [32:52<00:00, 1972.18s/it]

Found goal after: 	14.19 seconds,   	43723 state expanded (0.33 unique) 	 ~3082.05 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 100
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 1 games of avg length 100.0


{'simple': 40.0, 'unident_s': 40.0}

In [4]:
# CP+HPROXY horizon 400
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.74 seconds,   	7797 state expanded (0.33 unique) 	 ~2844.42 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.70 seconds,   	7826 state expanded (0.32 unique) 	 ~2893.27 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.60 seconds,   	7776 state expanded (0.33 unique) 	 ~2995.06 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.44 seconds,   	7591 state expanded (0.32 unique) 	 ~3112.38 expansions/s
First m

Found goal after: 	1.29 seconds,   	3478 state expanded (0.33 unique) 	 ~2695.30 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  23
Timestep: 46
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X Xoø20X X 
O ←1  →oO 
X       X 
X D X S X 


Found goal after: 	1.15 seconds,   	3478 state expanded (0.33 unique) 	 ~3036.89 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  23
Timestep: 47
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X Xoø20X X 
O ←o  →oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((3, 1), (1, 0)), ((1, 1), (-1, 0)))]
State of last node expanded:  Players: ((3, 1) facing (1, 0) holding onion@(3, 1), (1, 1) facing (-1, 0) holding onion@(1, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20), onion@(1, 0)], Order list: ['any', 'any']
Successors for last node expanded:  [((((3, 1), (1, 0)), ((1, 1), (-1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.Overco

Timestep: 131
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X Xoø20X X 
O   →o↑oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((3, 1), (1, 0)), ((1, 1), (-1, 0))), (((3, 1), (1, 0)), ((1, 1), (-1, 0)))]
State of last node expanded:  Players: ((3, 1) facing (1, 0) holding onion@(3, 1), (1, 1) facing (-1, 0) holding onion@(1, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20), onion@(1, 0)], Order list: ['any', 'any']
Successors for last node expanded:  [((((3, 1), (1, 0)), ((1, 1), (-1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f6949551dd0>, 1)]
COUPLED PLANNING FAILURE
failures:  108
Timestep: 132
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X Xoø20X X 
O   →o  O 
X     ↓oX 
X D X S X 


Path for last node expanded:  [None, (((3, 1), (1, 0)), ((1, 1), (-1, 0))), (((3, 1), (1, 0)), ((1, 1), (-1, 0)))]
State of last node expanded:  Players: ((3, 1) facing (1, 0) holding onion@(3, 1), (1, 1) facing (-1, 0) hol

...

Found goal after: 	8.15 seconds,   	34972 state expanded (0.36 unique) 	 ~4289.36 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 360
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø=↑o    X 
X     →dø20      X 
X X X D X D X X X 


Found goal after: 	6.68 seconds,   	28521 state expanded (0.37 unique) 	 ~4271.36 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 361
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø=←o    X 
X     →dø20      X 
X X X D X D X X X 


Found goal after: 	2.37 seconds,   	10200 state expanded (0.35 unique) 	 ~4301.98 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 362
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø1←0    X 
X     →sP   

Found goal after: 	0.49 seconds,   	1578 state expanded (0.40 unique) 	 ~3196.75 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 385
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     ↓dø7      X 
X X X D X D X X X 


Found goal after: 	0.24 seconds,   	1135 state expanded (0.42 unique) 	 ~4762.00 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 386
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     →dø8      X 
X X X D X D X X X 


Found goal after: 	0.17 seconds,   	789 state expanded (0.43 unique) 	 ~4624.34 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 387
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     →dø9     

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [36:56<00:00, 2216.75s/it]

Found goal after: 	0.03 seconds,   	124 state expanded (0.52 unique) 	 ~3729.10 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 392
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø14      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	102 state expanded (0.55 unique) 	 ~3809.68 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø15      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	90 state expanded (0.58 unique) 	 ~3634.26 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø16     

{'simple': 0.0, 'unident_s': 280.0}

In [5]:
# CP+HPROXY switched indices horizon 400
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.72 seconds,   	7797 state expanded (0.33 unique) 	 ~4533.25 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.99 seconds,   	7842 state expanded (0.32 unique) 	 ~3948.60 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.83 seconds,   	7612 state expanded (0.32 unique) 	 ~4161.98 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.72 seconds,   	7702 state expanded (0.32 unique) 	 ~4485.83 expansions/s
First mo

Found goal after: 	0.99 seconds,   	3383 state expanded (0.33 unique) 	 ~3405.20 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.78 seconds,   	3381 state expanded (0.33 unique) 	 ~4324.33 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.92 seconds,   	3379 state expanded (0.33 unique) 	 ~3689.16 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.80 seconds,   	3377 state expanded (0.33 unique) 	 ~4219.78 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.52 seconds,   	5617 state expanded (0.33 unique) 	 ~3690.91 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	1.02 seconds,   	5261 state expanded (0.33 unique) 	 ~5147.32 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.08 seconds,   	5188 state expanded (0.33 unique) 	 ~4819.24 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.13 seconds,   	5353 state expanded (0.33 unique) 	 ~4743.92 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	9.62 seconds,   	43723 state expanded (0.33 unique) 	 ~4544.73 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 368
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Found goal after: 	7.38 seconds,   	34334 state expanded (0.32 unique) 	 ~4652.16 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 369
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oø=←o    X 
X       ø-      X 
X X X D X D X X X 


Found goal after: 	4.50 seconds,   	21216 state expanded (0.33 unique) 	 ~4713.41 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 370
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø1←0    X 
X       ø-      X 
X X X D 

Found goal after: 	0.44 seconds,   	2389 state expanded (0.39 unique) 	 ~5440.16 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('stay', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1ø20↑d    X 
X       ø7      X 
X X X D X D X X X 


Found goal after: 	0.36 seconds,   	1952 state expanded (0.39 unique) 	 ~5381.71 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X   ←1  ø20↑d    X 
X       ø8      X 
X X X D X D X X X 


Found goal after: 	0.24 seconds,   	1280 state expanded (0.43 unique) 	 ~5238.41 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 395
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø20←d    X 
X       ø9      X 
X X X D X D X 

100%|█████████████████████████████████████████████████████████████████████████████████| 1/1 [1:11:21<00:00, 4281.68s/it]

Found goal after: 	0.14 seconds,   	676 state expanded (0.47 unique) 	 ~4805.16 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 398
Joint action taken: ('stay', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø20←d    X 
X     ↓1ø12      X 
X X X D X D X X X 


Found goal after: 	0.11 seconds,   	492 state expanded (0.51 unique) 	 ~4638.40 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 399
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1P ←s    X 
X       ø13      X 
X X X D X D X X X 


Found goal after: 	0.01 seconds,   	35 state expanded (0.54 unique) 	 ~4594.12 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 400
Joint action taken: ('→', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P   →s  X 
X     ↓1ø14      X 
X X X D X D X X

{'simple': 160.0, 'unident_s': 200.0}

Conclusions over num_games=1 :

CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple  : 0 -> 0 - failures 78
unidents: 40 -> 160 - failures 0

400 horizon

simple  : 0  -failures 378
unidents: 280 - failures 0

Switched indices CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple  : 40 -> 160 -failures 0
unidents: 40 -> 160 - failures 0

400 horizon

simple  : 160 - failures 0
unidents: 200 - failures 0

In [6]:
# CP+HPROXY horizon 100, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.00 seconds,   	7797 state expanded (0.33 unique) 	 ~3899.17 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.72 seconds,   	7826 state expanded (0.32 unique) 	 ~4559.16 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.73 seconds,   	7776 state expanded (0.33 unique) 	 ~4498.35 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.72 seconds,   	7591 state expanded (0.32 unique) 	 ~4409.92 expansions/s
First m

 20%|█████████████████                                                                    | 1/5 [00:35<02:21, 35.41s/it]

Found goal after: 	1.14 seconds,   	5161 state expanded (0.33 unique) 	 ~4537.61 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 22
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø3X X 
O ←o  →oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 

...

Found goal after: 	9.69 seconds,   	43962 state expanded (0.36 unique) 	 ~4538.59 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 45
Joint action taken: ('↓', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P     ↓0X 
X     →oø17      X 
X X X D X D X X X 


Found goal after: 	9.58 seconds,   	44427 state expanded (0.36 unique) 	 ~4637.27 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 46
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P   ←0  X 
X     →oø18      X 
X X X D X D X X X 


Found goal after: 	9.35 seconds,   	39671 state expanded (0.36 unique) 	 ~4243.31 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 47
Joint action taken: ('←', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ←0    X 
X     →oø19      X 
X X X D X D X X

Found goal after: 	12.86 seconds,   	57333 state expanded (0.34 unique) 	 ~4457.88 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 70
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X ↓o    ø12    ↓0X 
X       P       X 
X X X D X D X X X 


Found goal after: 	11.80 seconds,   	53714 state expanded (0.34 unique) 	 ~4552.54 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 71
Joint action taken: ('←', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø13  ←0  X 
X ↓o    P       X 
X X X D X D X X X 


Found goal after: 	11.95 seconds,   	53714 state expanded (0.34 unique) 	 ~4495.80 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 72
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø14←0    X 
X ↓o    P       X 
X X X D X D X

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [5:26:00<00:00, 3912.07s/it]

Found goal after: 	0.06 seconds,   	308 state expanded (0.49 unique) 	 ~4871.82 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 96
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑dø20      X 
X       ø15←d    X 
X X X D X D X X X 


Found goal after: 	0.05 seconds,   	211 state expanded (0.56 unique) 	 ~4548.04 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 97
Joint action taken: ('↑', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20↑d    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	67 state expanded (0.79 unique) 	 ~3305.05 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 98
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20←d    X 
X       ø17      X 
X X X D X D X X 

{'simple': 0.0, 'unident_s': 40.0}

In [7]:
# CP+HPROXY (switch indices) horizon 100, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.72 seconds,   	7797 state expanded (0.33 unique) 	 ~4534.06 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.76 seconds,   	7842 state expanded (0.32 unique) 	 ~4450.28 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.92 seconds,   	7612 state expanded (0.32 unique) 	 ~3960.42 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.75 seconds,   	7702 state expanded (0.32 unique) 	 ~4397.40 expansions/s
First mo

Found goal after: 	0.82 seconds,   	3383 state expanded (0.33 unique) 	 ~4120.41 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.80 seconds,   	3381 state expanded (0.33 unique) 	 ~4210.59 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.77 seconds,   	3379 state expanded (0.33 unique) 	 ~4374.58 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.80 seconds,   	3377 state expanded (0.33 unique) 	 ~4240.53 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.37 seconds,   	5617 state expanded (0.33 unique) 	 ~4099.38 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	1.17 seconds,   	5261 state expanded (0.33 unique) 	 ~4505.45 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.15 seconds,   	5188 state expanded (0.33 unique) 	 ~4506.03 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.18 seconds,   	5353 state expanded (0.33 unique) 	 ~4541.18 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	0.70 seconds,   	3852 state expanded (0.37 unique) 	 ~5520.84 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø6      X 
X       ø20↓d    X 
X X X D X D X X X 


Found goal after: 	0.33 seconds,   	2015 state expanded (0.35 unique) 	 ~6015.04 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø7↑d    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.29 seconds,   	1716 state expanded (0.36 unique) 	 ~5999.40 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø8↑d    X 
X       ø20      X 
X

Found goal after: 	20.34 seconds,   	87961 state expanded (0.35 unique) 	 ~4324.08 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('→', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø-    →sX 
X       P       X 
X X X D X D X X X 


Found goal after: 	10.20 seconds,   	44530 state expanded (0.35 unique) 	 ~4364.52 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('↑', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X ↑sS 
X   ←1  ø-      X 
X       P       X 
X X X D X D X X X 


Found goal after: 	10.62 seconds,   	47192 state expanded (0.35 unique) 	 ~4443.20 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('→', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X →sS 
X ←1    ø-      X 
X       P       X 
X X X D X D X X 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [1:46:19<00:00, 1275.91s/it]

Found goal after: 	8.90 seconds,   	43723 state expanded (0.33 unique) 	 ~4913.24 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 100
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 5 games of avg length 100.0


{'simple': 40.0, 'unident_s': 40.0}

In [8]:
# CP+HPROXY horizon 400, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.78 seconds,   	7797 state expanded (0.33 unique) 	 ~4386.85 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.70 seconds,   	7826 state expanded (0.32 unique) 	 ~4610.06 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.71 seconds,   	7776 state expanded (0.33 unique) 	 ~4550.11 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.77 seconds,   	7591 state expanded (0.32 unique) 	 ~4279.32 expansions/s
First m

Timestep: 128
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((3, 1), (1, 0))), (((2, 1), (0, -1)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((2, 1) facing (0, -1) holding onion@(2, 1), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((3, 1), (1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f690a4a3350>, 1)]
COUPLED PLANNING FAILURE
failures:  107
Timestep: 129
Joint action taken: ('→', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X     →oX 
X D X S X 


Path for last node expanded:  [None, (((3, 1), (1, 0)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((3, 2) facing (1, 0) holding onion@(3, 2), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state ('

Timestep: 250
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   ↑o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (0, -1) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((2, 1), (0, -1))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f691d4878d0>, 1)]
COUPLED PLANNING FAILURE
failures:  229
Timestep: 251
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   ↑o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (0, -1) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['a

...

Found goal after: 	0.02 seconds,   	86 state expanded (0.80 unique) 	 ~3668.48 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 355
Joint action taken: ('↑', 'interact') 	 Reward: 20 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑1ø-↑0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	8.48 seconds,   	44890 state expanded (0.36 unique) 	 ~5294.82 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 356
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø-↑o    X 
X     ↓1ø20      X 
X X X D X D X X X 


Found goal after: 	7.29 seconds,   	40670 state expanded (0.36 unique) 	 ~5579.75 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 357
Joint action taken: ('←', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø-←o    X 
X     ↓dø20      

Found goal after: 	1.58 seconds,   	9940 state expanded (0.34 unique) 	 ~6272.21 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 380
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø19↑0    X 
X       ø2      X 
X X X D X D X X X 


Found goal after: 	1.44 seconds,   	9381 state expanded (0.34 unique) 	 ~6501.21 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 381
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø20↑o    X 
X       ø3      X 
X X X D X D X X X 


Found goal after: 	0.88 seconds,   	5464 state expanded (0.36 unique) 	 ~6181.42 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 382
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     ↓dø4      X 
X

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [2:36:58<00:00, 1883.66s/it]

Found goal after: 	0.01 seconds,   	27 state expanded (1.00 unique) 	 ~3086.06 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (0, -1)))
failures:  0
Timestep: 400
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →sP ←o    X 
X       ø20      X 
X X X D X D X X X 


Avg reward 280.00 (std: 0.00, se: 0.00) over 5 games of avg length 400.0


{'simple': 0.0, 'unident_s': 280.0}

In [9]:
# CP+HPROXY (switch indices) horizon 400, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.41 seconds,   	7797 state expanded (0.33 unique) 	 ~5521.33 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.38 seconds,   	7842 state expanded (0.32 unique) 	 ~5700.89 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.39 seconds,   	7612 state expanded (0.32 unique) 	 ~5492.29 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.44 seconds,   	7702 state expanded (0.32 unique) 	 ~5366.08 expansions/s
First mo

Found goal after: 	0.67 seconds,   	3383 state expanded (0.33 unique) 	 ~5020.60 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.67 seconds,   	3381 state expanded (0.33 unique) 	 ~5057.44 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.68 seconds,   	3379 state expanded (0.33 unique) 	 ~4987.85 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.61 seconds,   	3377 state expanded (0.33 unique) 	 ~5571.32 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.04 seconds,   	5617 state expanded (0.33 unique) 	 ~5408.84 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	0.97 seconds,   	5261 state expanded (0.33 unique) 	 ~5429.61 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	0.99 seconds,   	5188 state expanded (0.33 unique) 	 ~5265.67 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	0.96 seconds,   	5353 state expanded (0.33 unique) 	 ~5557.24 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	32.33 seconds,   	186801 state expanded (0.30 unique) 	 ~5777.61 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 351
Joint action taken: ('↑', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ↑0    X 
X     →oP       X 
X X X D X D X X X 


Found goal after: 	31.21 seconds,   	186826 state expanded (0.30 unique) 	 ~5986.67 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 352
Joint action taken: ('stay', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ↑0    X 
X       P       X 
X X X D X D X X X 


Found goal after: 	31.08 seconds,   	186714 state expanded (0.30 unique) 	 ~6007.14 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 353
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oP ↑o    X 
X       P       X 
X X X 

Found goal after: 	1.55 seconds,   	9767 state expanded (0.37 unique) 	 ~6294.12 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (0, 1)))
failures:  0
Timestep: 376
Joint action taken: ('stay', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø7      X 
X     ↓1ø=↓0    X 
X X X D X D X X X 


Found goal after: 	1.86 seconds,   	9894 state expanded (0.37 unique) 	 ~5306.87 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 377
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1ø8      X 
X       ø=↓d    X 
X X X D X D X X X 


Found goal after: 	2.39 seconds,   	14976 state expanded (0.37 unique) 	 ~6274.30 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 378
Joint action taken: ('↑', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X   ←1  ø9↑d    X 
X       ø=      X 
X X X D X D 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [4:42:34<00:00, 3390.80s/it]

Found goal after: 	0.11 seconds,   	676 state expanded (0.47 unique) 	 ~6022.01 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 398
Joint action taken: ('stay', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø20←d    X 
X     ↓1ø12      X 
X X X D X D X X X 


Found goal after: 	0.09 seconds,   	492 state expanded (0.51 unique) 	 ~5551.56 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 399
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1P ←s    X 
X       ø13      X 
X X X D X D X X X 


Found goal after: 	0.01 seconds,   	35 state expanded (0.54 unique) 	 ~5637.29 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 400
Joint action taken: ('→', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P   →s  X 
X     ↓1ø14      X 
X X X D X D X X

{'simple': 160.0, 'unident_s': 200.0}

Conclusions over num_games=5 :

CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple : Avg reward 8.00 (std: 16.00, se: 7.16), 2nd : avg 0: failures 390/500
unidents: Avg reward 40.00 (std: 0.00, se: 0.00) - failures 0


400 horizon

simple : Avg reward 108.00 (std: 88.18, se: 39.44), 2nd: 36 (std:72, se: 32.20) - failures 1550/2000
unidents: Avg reward 280.00 (std: 0.00, se: 0.00) - failures 0

Switched indices CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple : Avg reward 40.00 (std: 0.00, se: 0.00) - failures 0
unidents: Avg reward 40.00 (std: 0.00, se: 0.00) - failures 0

400 horizon

simple : Avg reward 160.00 (std: 0.00, se: 0.00) -failures 0
unidents: Avg reward 200.00 (std: 0.00, se: 0.00) -failures 0
